# London AirBnB Data Analysis

## Context
London is one of AirBnB's largest markets, with over 70,000 properties listed on the site. Travel and tourism have been impacted signficantly by the global pandemic - the first confirmed case was in January 2020, and the government issued a country wide lockdown in late March that year, restricting travel to essential trips only. Restrictions began to be lifted in June, and with limited international travel option restricted over the summar months, many have chosen to take 'staycations' instead of staying abroad. The last few months of AirBnB data may therefore provide insight into the impact that this uncertain environment has had on travel and tourism wihtin London.  


## Purpose 
The purpose of this notebook is to perform data analysis looking at the impact of the global pandemic and lockdown in London on demand for and supply of AirBnB listings. 
  
The following analysis is based on data from AirBnB listings in London, taken from InsideAirBnB. It looks at changes in pricing, property availability and minimum stay requirements. Three questions are asked:
1. Pricing - 
    - Was last minute discounting of listings more common amongst hosts during the lockdown months, and were listings discounted more signficantly than usual?
2. Property availability -
    - Is there a trend of hosts removing their listings from AirBnB or making them unavailable for booking following the lockdown months? 
3. Minimum stay requirements - 
    - Is there a trend of an increase in the minimum stay at listings to cover for the increased effort to facilitate new guests, e.g. higher cleaning costs? 

## Methodology
The data was obtained from AirBnB inside data and COVID data. This was unzipped etc., ingested and processed in the London AirBnB Data Processing notebook. In this analysis, 3-4 high level steps are taken for each question:
1. Aggregated processing datasets are created containing data requires for analysis 
1. Analysis datasets are created through data wrangling, joining etc. 
2. Charts are created to visualise the changes in the question area
3. Conclusions are drawn from analysis  

## Results
The analysis suggests the following trends in the areas of question:
- Pricing - the analysis showed that more properties did apply last minute discounting around the lockdown months of March & April than in the prior months. The analysis also showed that the discount rate that could be achieved through last minute bookings was highest in June, and that the number of listings a host has was correlated with the rate of discount. To validate these findings, analysis on pricing data from prior years would be required to validate that this was not a seaonal trend. 
- Property availability - the analysis showed that there was a trend of an increased proportion of hosts marking their listings as unavailable in the lockdown months of March & April. It was also shown that since April, there has been a downward trend in the volume of London listings on the site, with a signficant drop off in August 2020.
- Minimum stay - the analysis showed that until March 2020, there were more properties with a minimum stay of 4-6 nights than 7 nights, and from April onwards there were more properties with a minimum stay of 7 nights.  


## Further areas for analysis
Other areas that could be interesting to investigate with the London data include: 
- What have the trends been in property cancellation and has this correlated with hosts making their properties unavailable?
- Has there been any trend in what guests reference in a positive review? E.g. have there been an increase in the proportion of positive or negative reviews that reference work from home capabilities? 
- Has the maximum number of nights for stay gone up to cater for consumers that are looking to do long term working from an AirBnB property? 

The analysis has been focused on data from AirBnB London listings, and further insight could be gained from integrating the dataset with further sources, e.g.
- AirBnB listing data from other cities - asessing whether the trends identified in London are consistent with other European capital cities
- COVID cases - does the number of cases of COVID in an area have an impact on any of the trends identified? 

N.B. This analysis was exploratory in nature to examine potential trends in the areas of question, and the trends identified were not proven to be statistically robust. Further analysis could look to develop hypothesis in each of the areas and test them for statistical signifance. 


# Set up

## Library import

In [1]:
# Data manipulation
import pandas as pd
import numpy as np
from datetime import date, time, timedelta
import datetime as dt
import matplotlib.pyplot as plt
from IPython.display import display, HTML
import re 

# Options for pandas
pd.options.display.max_columns = 50
pd.options.display.max_rows = 30

# Visualizations
import plotly
import plotly.graph_objs as go
import plotly.offline as ply
plotly.offline.init_notebook_mode(connected=True)
import plotly.express as px
import seaborn as sns
%matplotlib inline

# Visualisation options
sns.set_style("whitegrid")

# Hide warnings 
import warnings 
warnings.simplefilter('ignore')

# Autoreload extension
if 'autoreload' not in get_ipython().extension_manager.loaded:
    %load_ext autoreload
    
%autoreload 2


# Another try
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## Local library import

In [2]:
import sys
import os

# Find local library directory - which should be located within a parent directory
current_path = os.getcwd()
os.chdir("..")
current_path = os.getcwd() 
libfiledir = "library"

current_path
direxists = False
while direxists==False:
    test_dir = os.path.join(current_path,libfiledir)
    last_current_path = current_path
    direxists = os.path.isdir(test_dir)
    current_path = os.path.dirname(current_path)
    if(current_path == last_current_path):
        break;
        
if direxists == True:
    sys.path.append(test_dir)
    
from dataframe_common import *

# Data ingestion / import set-up

## Review of source data files

The files were downloaded from the Inside AirBnB [website](http://insideairbnb.com/get-the-data.html.) on 27th August 2020.  The files were processed in the processing notebook and then outputted in the tmp directory to feather format for faster ingestion.

The data directory contains subdirectories for each of the periods where data was downloaded.

In [3]:
data_dir = 'data/AirBnB-Data-040920'
!ls {data_dir}

2019_07_10         2019_11_05         2020_03_15         2020_08_24
2019_08_09         2019_12_09         2020_04_14         Neighbourhood_data
2019_09_14         2020_01_09         2020_05_10
2019_10_15         2020_02_16         2020_06_11


In [4]:
periods = ! ls {data_dir}
periods.remove('Neighbourhood_data')

The tmp directory contains the procesed data files. These include the period in the file name.

In [5]:
tmp_dir = 'tmp'
processed_data = 'processed_data'
file_types = {'feather':'.feather','csv':'.csv'}
! ls {tmp_dir}/{processed_data}

2019_07_10calendar_det.feather 2020_02_16listings.feather
2019_07_10listings.feather     2020_03_15calendar_det.feather
2019_08_09calendar_det.feather 2020_03_15listings.feather
2019_08_09listings.feather     2020_04_14calendar_det.feather
2019_09_14calendar_det.feather 2020_04_14listings.feather
2019_09_14listings.feather     2020_05_10calendar_det.feather
2019_10_15calendar_det.feather 2020_05_10listings.feather
2019_10_15listings.feather     2020_06_11calendar_det.feather
2019_11_05calendar_det.feather 2020_06_11listings.feather
2019_11_05listings.feather     2020_08_24calendar_det.feather
2019_12_09calendar_det.feather 2020_08_24listings.feather
2019_12_09listings.feather     all_listings.csv
2020_01_09calendar_det.feather all_listings.feather
2020_01_09listings.feather     all_listings_price.feather
2020_02_16calendar_det.feather list_price_avail_grped.feather


Function is created to read in a specified file / period of data.

In [6]:
def get_data(filename,period,**kwargs):
    cols = kwargs.get('cols', None)
    df = pd.read_feather(os.path.join(tmp_dir,processed_data,period + filename + file_types['feather']),
                         columns=cols)
    if 'date' in df.columns:
        df['date'] = pd.to_datetime(df['date'])
    return df

# Data analysis 

## Pricing

### Has there been an increase in the proportion of listings with "last minute deals"? Are discounts more substantial than they were previouly?

Research has noted that, much line airline tickets, deals can be achieved by savvy holiday-goers who wait until the last minute before booking their stay, as opposed to booking months in advance. Has last minute discounting of properties become more common amongst host following the pandemic, and are discounts more sustantial than they were previouly?

This analysis compares the price of properties advertised 3 months prior to stay date (in advance) to 1 month prior to stay daet (last minute). 

#### Create aggregated processed dataset

The objective of this step is to create a dataframe which has all London properties that were listed at some point in the year on AirBnB, and the price that they were listed at the various points when the data was scraped. 

###### Create list of all properties that were listed 

Function created to iterate through the periods, retrive the listing ID from the calendar data file, and create a list of unique listings.

In [7]:
def get_all_listing_ids(period):
    ''' Creates dataframe of all London listing IDs'''
    cal_list = pd.DataFrame(columns=['listing_id'])
    for period in periods:
        calendar = get_data('calendar_det',period,cols=['listing_id'])
        calendar.drop_duplicates(inplace=True)
        cal_list = cal_list.append(calendar,ignore_index=True)
        cal_list.drop_duplicates(inplace=True)
    return cal_list

In [8]:
%%time
cal_list = get_all_listing_ids(periods)

CPU times: user 12.7 s, sys: 7.14 s, total: 19.8 s
Wall time: 27.2 s


The output is a one column dataframe with all uique listings from the year.

In [9]:
cal_list.head(5)

listing_id
0      78892
1     157536
2      13913
3      79129
4     157714

In [10]:
cal_list.shape

(134752, 1)

In [11]:
assert len(cal_list) == cal_list['listing_id'].nunique()

##### Add on month and year combinations to listing ID dataframe

Dataframes are created containing the months and years needed - those from when the data has been scraped.

In [12]:
months = pd.DataFrame(data={'date_month': [1,2,3,4,5,6,7,8,9,10,11,12]})
years = pd.DataFrame(data={'date_year': [2019,2020]})
months['key']=1
years['key']=1
months_years = months.merge(years,how='outer',on='key')

In [13]:
months_years.sample(2)

date_month  key  date_year
12           7    1       2019
17           9    1       2020

This is outer joined to the key of '1' to ensure a listing ID for each month / date year combination. 

In [14]:
cal_list['key'] = 1
all_lists_mon_year = cal_list.merge(months_years,how='left',on='key')

The result is a dataframe containing 24 rows for each listing ID.

In [15]:
all_lists_mon_year.query('listing_id == 78892').T

0      1      2      3      4      5      6      7      8   \
listing_id  78892  78892  78892  78892  78892  78892  78892  78892  78892   
key             1      1      1      1      1      1      1      1      1   
date_month      1      1      2      2      3      3      4      4      5   
date_year    2019   2020   2019   2020   2019   2020   2019   2020   2019   

               9      10     11     12     13     14     15     16     17  \
listing_id  78892  78892  78892  78892  78892  78892  78892  78892  78892   
key             1      1      1      1      1      1      1      1      1   
date_month      5      6      6      7      7      8      8      9      9   
date_year    2020   2019   2020   2019   2020   2019   2020   2019   2020   

               18     19     20     21     22     23  
listing_id  78892  78892  78892  78892  78892  78892  
key             1      1      1      1      1      1  
date_month     10     10     11     11     12     12  
date_year    2019   2020   2019   2020   2019   2020

In [16]:
assert len(cal_list) * 24 == len(all_lists_mon_year)

This is outputted to temporary directory for faster future loading. 

In [17]:
all_lists_mon_year.to_feather(os.path.join(tmp_dir,processed_data,'all_listings' + file_types['feather']))

##### Map on pricing data

In [18]:
all_lists_mon_year.head(3)

listing_id  key  date_month  date_year
0      78892    1           1       2019
1      78892    1           1       2020
2      78892    1           2       2019

Now have 1 column dataframe containing all the listings that were throughout the year and a date month / year column. Want to add to this the price that the listings was advertised at the month / year that the data was scrapped.

First step is to create a dictionary mapping the dates that the data was scraped to summary dates.

In [19]:
periods_dict = {'2019_07_10':'July 2019',
 '2019_08_09':'August 2019',
 '2019_09_14':'September 2019',
 '2019_10_15':'October 2019',
 '2019_11_05':'November 2019',
 '2019_12_09':'December 2019',
 '2020_01_09':'January 2020',
 '2020_02_16':'February 2020',
 '2020_03_15':'March 2020',
 '2020_04_14':'April 2020',
 '2020_05_10':'May 2020',
 '2020_06_11':'June 2020',
 '2020_08_24':'August 2020'}

Function is created to iterate through the periods, get the calendar data from that month, aggregate it - count of days available and median price, and then map it back to the dataframe with all listings and months years.

In [20]:
def agg_cal_data(periods_dict,all_listings):
    ''' Takes in dictionary with periods and listings dataframe and maps on monthly prices '''
    for exact_date,summary_date in periods_dict.items():
        print(f'Processeing period {summary_date}')
        cal = get_data('calendar_det',exact_date)
        cal_grp = cal.groupby(['listing_id','date_month','date_year']).agg(**{f'{summary_date}_days_available':('available','sum'),
                                                           f'{summary_date}_median_price':('price','median')}).reset_index()
        all_listings = all_listings.merge(cal_grp,how='left',on=['listing_id','date_year','date_month'])
        print(f'Processed period {summary_date}')        
    return all_listings

In [21]:
%%time
list_price_avail_grped = agg_cal_data(periods_dict,all_lists_mon_year)

Processeing period July 2019
Processed period July 2019
Processeing period August 2019
Processed period August 2019
Processeing period September 2019
Processed period September 2019
Processeing period October 2019
Processed period October 2019
Processeing period November 2019
Processed period November 2019
Processeing period December 2019
Processed period December 2019
Processeing period January 2020
Processed period January 2020
Processeing period February 2020
Processed period February 2020
Processeing period March 2020
Processed period March 2020
Processeing period April 2020
Processed period April 2020
Processeing period May 2020
Processed period May 2020
Processeing period June 2020
Processed period June 2020
Processeing period August 2020
Processed period August 2020
CPU times: user 2min 2s, sys: 2min 6s, total: 4min 8s
Wall time: 4min 29s


Human readable month / year column is added to the dataframe.

In [22]:
def mon_year(df):
    ''' Takes in calendar df and outputs a cleaned month / year col '''
    if df['date_month'] == 1 and df['date_year'] == 2019:
        return 'January 2019'
    elif df['date_month'] == 2 and df['date_year'] == 2019:
        return 'February 2019'
    elif df['date_month'] == 3 and df['date_year'] == 2019:
        return 'March 2019'
    elif df['date_month'] == 4 and df['date_year'] == 2019:
        return 'April 2019'
    elif df['date_month'] == 5 and df['date_year'] == 2019:
        return 'May 2019'
    elif df['date_month'] == 6 and df['date_year'] == 2019:
        return 'June 2019'
    elif df['date_month'] == 7 and df['date_year'] == 2019:
        return 'July 2019'
    elif df['date_month'] == 8 and df['date_year'] == 2019:
        return 'August 2019'
    elif df['date_month'] == 9 and df['date_year'] == 2019:
        return 'September 2019'
    elif df['date_month'] == 10 and df['date_year'] == 2019:
        return 'October 2019'
    elif df['date_month'] == 11 and df['date_year'] == 2019:
        return 'November 2019'
    elif df['date_month'] == 12 and df['date_year'] == 2019:
        return 'December 2019'
    elif df['date_month'] == 1 and df['date_year'] == 2020:
        return 'January 2020'
    elif df['date_month'] == 2 and df['date_year'] == 2020:
        return 'February 2020'
    elif df['date_month'] == 3 and df['date_year'] == 2020:
        return 'March 2020'
    elif df['date_month'] == 4 and df['date_year'] == 2020:
        return 'April 2020'
    elif df['date_month'] == 5 and df['date_year'] == 2020:
        return 'May 2020'
    elif df['date_month'] == 6 and df['date_year'] == 2020:
        return 'June 2020'
    elif df['date_month'] == 7 and df['date_year'] == 2020:
        return 'July 2020'
    elif df['date_month'] == 8 and df['date_year'] == 2020:
        return 'August 2020'
    elif df['date_month'] == 9 and df['date_year'] == 2020:
        return 'September 2020'
    elif df['date_month'] == 10 and df['date_year'] == 2020:
        return 'October 2020'
    elif df['date_month'] == 11 and df['date_year'] == 2020:
        return 'November 2020'
    elif df['date_month'] == 12 and df['date_year'] == 2020:
        return 'December 2020'
    else:
        return 'TBC'

In [23]:
list_price_avail_grped['mon_year'] = list_price_avail_grped.apply(mon_year,axis=1) 

Dataframe is outputted to temporary directory for faster subsequent processing.

In [24]:
list_price_avail_grped.to_feather(os.path.join(tmp_dir,processed_data,'list_price_avail_grped' + file_types['feather']))

#### Create analytics dataset

The objective of this step is to create a dataframe which for each month  of 2020 shows:
- the number of listings that changed the prices when advertised in advance (3 months prior to stay date) vs. last minute (1 month prior to stay date) "price change"
- whether shoppers would have made a saving or loss from booking the property at the last minute "price change cat"
- what the price change was for that category, i.e. the average saving or loss rate that shoppers had

In [25]:
listing_avail_prices = pd.read_feather(os.path.join(tmp_dir,processed_data,'list_price_avail_grped' + file_types['feather']))

First a dictionary is created containing the month of booking as the key and the months advertised (3 months prior or 1 month prior) as the values. 

In [26]:
# Set dict with month and 1 month before and 3 month prior
mon_3m_1m = {'January 2020':['October 2019','December 2019'],
'February 2020':['November 2019','January 2020'],
'March 2020':['December 2019','February 2020'],
'April 2020':['January 2020','March 2020'],
'May 2020':['February 2020','April 2020'],
'June 2020':['March 2020','May 2020'],
'July 2020':['April 2020','January 2020'],
'August 2020':['May 2020','June 2020']}

In [75]:
### TODO - break out into separate functions
agg_df = pd.DataFrame()
for k,v in mon_3m_1m.items():
    ''' Iterates through dataframe and creates columns based on if price has changed and in which direction'''
    print(f'Processing data for {k}')
    # First filter to the relevant month
    df = listing_avail_prices[listing_avail_prices['mon_year']==k]
    
    # Create list of columns for aggregation and select just these columns 
    median_price = [col + '_median_price' for col in v]
    days_available =  [col + '_days_available' for col in v]
    df = df[['listing_id'] + median_price + days_available ]
    
    # Filer out cases where days available is null or 0 for 3 months or 1 month out
    df = df[(df[days_available[0]].notnull()) &
            (df[days_available[1]].notnull()) & 
            (df[days_available[0]]!=0) & 
            (df[days_available[1]]!=0)] 
    # Create required columns
    # 1/3 - price change
    df['price_change'] = np.where(df[median_price[0]] == df[median_price[1]],0,1)
    # 2/3 - last min shopping -> saving, loss or no change 
    df['price_change_cat'] = np.where(df[median_price[0]] > df[median_price[1]],'Saving',
                                      (np.where(df[median_price[1]] > df[median_price[0]],'Loss','No change')))
    # 3/3 - last min shopping -> saving, loss or no change 
    df['price_change_rate'] = df[median_price[0]]/ df[median_price[1]] - 1
    
     # Group by the price change category and aggregate
    df_grp = df.groupby(['price_change_cat']).agg(**{'number_listings':('listing_id','count'),
                                           'median_price_change_rate':('price_change_rate','median')}).reset_index()
    df_grp['proportion'] =  df_grp['number_listings']/ df_grp['number_listings'].sum()
    df_grp['period'] = k
    
    agg_df = agg_df.append(df_grp)
print("Processed")

Processing data for January 2020
Processing data for February 2020
Processing data for March 2020
Processing data for April 2020
Processing data for May 2020
Processing data for June 2020
Processing data for July 2020
Processing data for August 2020
Processed


The resulting dataframe contains:
- volume and proportion of listings where there would have been a loss or saving for last minute booking stay in the month
- the median price change - i.e. the average saving or loss rate

In [76]:
agg_df.rename(columns={'price_change_cat':'Last minute price change category',
                      'number_listings':'Number of listings',
                      'median_price_change_rate':'Last minute price change rate',
                      'proportion':'Proportion of listings',
                      'period':'Period'},inplace=True)

In [77]:
agg_df

Last minute price change category  Number of listings  \
0                              Loss                4461   
1                         No change               24371   
2                            Saving                7754   
0                              Loss                3905   
1                         No change               21939   
2                            Saving                8466   
0                              Loss                3972   
1                         No change               21248   
2                            Saving                9109   
0                              Loss                3816   
1                         No change               21962   
2                            Saving                9819   
0                              Loss                2156   
1                         No change               24354   
2                            Saving                8965   
0                              Loss                1069   
1                         No change               28898   
2                            Saving                7720   
0                              Loss                5753   
1                         No change               16922   
2                            Saving                3576   
0                              Loss                1519   
1                         No change               34605   
2                            Saving                3850   

   Last minute price change rate  Proportion of listings         Period  
0                      -0.109091                0.121932   January 2020  
1                       0.000000                0.666129   January 2020  
2                       0.160169                0.211939   January 2020  
0                      -0.109489                0.113815  February 2020  
1                       0.000000                0.639435  February 2020  
2                       0.166667                0.246750  February 2020  
0                      -0.101868                0.115704     March 2020  
1                       0.000000                0.618952     March 2020  
2                       0.166667                0.265344     March 2020  
0                      -0.102564                0.107200     April 2020  
1                       0.000000                0.616962     April 2020  
2                       0.214876                0.275838     April 2020  
0                      -0.111111                0.060775       May 2020  
1                       0.000000                0.686512       May 2020  
2                       0.428571                0.252713       May 2020  
0                      -0.107143                0.028365      June 2020  
1                       0.000000                0.766790      June 2020  
2                       0.461901                0.204845      June 2020  
0                      -0.153846                0.219154      July 2020  
1                       0.000000                0.644623      July 2020  
2                       0.146667                0.136223      July 2020  
0                      -0.114286                0.038000    August 2020  
1                       0.000000                0.865688    August 2020  
2                       0.200000                0.096313    August 2020

#### Create visualisations

##### Proportion of listings applying a last minute price decrease or increase to booking

In [81]:
agg_df
fig = px.bar(agg_df,x='Period',y='Proportion of listings',color='Last minute price change category',
            color_discrete_sequence=px.colors.qualitative.Dark24,
          )
fig.update_layout(title='Proportion of listings applying a decrease or increase to booking at last minute compared to 3 months<br>in advance')

In [79]:
fig = px.line(agg_df,x='Period',y='Last minute price change rate',color='Last minute price change category',
         color_discrete_sequence=px.colors.qualitative.Dark24)
fig.update_layout(title='Saving or loss rate from "last minute shopping" - advertised prices 3 months prior vs. 1 month prior ')
fig.show()

#### Conclusion

The first chart shows that an increased proportion of listings offered a “last minute discount” in the months between January - April. This trend supports our initial hypothesis that more hosts would be discounting their properties during the lockdown months in an attempt to try and secure bookings when there was less consumer confidence in travel and spending more broadly. 

The first chart also shows the trend as reversed from April onwards. Intuitively this makes sense, as we come into the UK holiday season, and with internatioanl travel options limited, there was likely increased demand for UK properties, and therefore less hosts applied "last minute" discounts to their properties. 

This second chart shows that the saving rate from last minute shopping was most pronounced in the months of May and June, with a saving rate of 46%. So while there was a decrease in the proportion of properties offering a last minute discount from April onwards, the rate at which this discount was being applied was greatest in May and June.

##### One-off analysis on June months

Given that when applied, the discount rate was greatest in June, it may be interesting to look at which properties are being discounted most heavily. Is the discount rate due to a number of outlier listings being heavily discounted, or is it part of a more general trend?

First filter the listings_avail_prices dataframe to June months and select the relevant columns for in advance (3 months) and last minute (1 month) pricing.

In [32]:
listing_avail_prices_jun_20 = listing_avail_prices.query('mon_year == "June 2020"')

In [33]:
listing_avail_prices_jun_20 = listing_avail_prices_jun_20[['March 2020_median_price','May 2020_median_price','March 2020_days_available','May 2020_days_available','listing_id']]

In [34]:
listing_avail_prices_jun_20 = listing_avail_prices_jun_20[(listing_avail_prices_jun_20['March 2020_days_available'].notnull()) &
                            (listing_avail_prices_jun_20['May 2020_days_available'].notnull()) &
                            (listing_avail_prices_jun_20['March 2020_days_available'] != 0) &
                            (listing_avail_prices_jun_20['May 2020_days_available'] != 0)]                                                        

In [35]:
listing_avail_prices_jun_20.head(2)

March 2020_median_price  May 2020_median_price  March 2020_days_available  \
35                     52.0                   52.0                       27.0   
59                     49.0                   49.0                       30.0   

    May 2020_days_available  listing_id  
35                     28.0      157536  
59                     30.0       13913

Then read in the listings data from the period to add on the number of properties the host lists on the site. 

In [36]:
listings_jun_20 = pd.read_feather(os.path.join(tmp_dir,processed_data,'2020_06_11listings.feather'))

In [37]:
listings_jun_20.head(2)

listing_id        room_type  calculated_host_listings_count
0       11551  Entire home/apt                               2
1       13913     Private room                               3

Merge this onto the listing availability prices dataframe.

In [38]:
listing_avail_prices_jun_20 = listing_avail_prices_jun_20.merge(listings_jun_20[['listing_id','calculated_host_listings_count']],how='left',on='listing_id')

Then bin the host listing count.

In [39]:
def bin_host_list_count(calc_host_listings_count):
    ''' Takes in a number column and outputs a binned category'''
    if calc_host_listings_count in [1,2]: return '1-2'
    elif calc_host_listings_count in [3,4,5,6,7,8,9]: return '3-9'
    else: return '10+'

In [40]:
listing_avail_prices_jun_20['Host no. of listings'] = listing_avail_prices_jun_20['calculated_host_listings_count'].apply(bin_host_list_count)

Finally plot the results

In [41]:
listing_avail_prices_jun_20.head(2)

March 2020_median_price  May 2020_median_price  March 2020_days_available  \
0                     52.0                   52.0                       27.0   
1                     49.0                   49.0                       30.0   

   May 2020_days_available  listing_id  calculated_host_listings_count  \
0                     28.0      157536                             2.0   
1                     30.0       13913                             3.0   

  Host no. of listings  
0                  1-2  
1                  3-9

In [73]:
fig = px.scatter(listing_avail_prices_jun_20.query('`March 2020_median_price` <= 3000 and `May 2020_median_price` <= 3000  '),x='March 2020_median_price',y='May 2020_median_price',
          trendline='ols',
          hover_data=['listing_id'],
          color='Host no. of listings')

fig.update_layout(title='June stay listing price as advertised in March vs. May, by host listing count')
fig.update_xaxes(title='Avg. price of property adv. in March 2020')
fig.update_yaxes(title='Avg. price of property adv. in May 2020')
fig.show()

It can be seen that there is correlation between the number of properties the host has and their propensity to discount. Intuitively this makes sense, as one would assume that the hosts with more listings are more likely to be commercial business that want to fill them all to secure cash flow certainty. They may also have greater margins and so be able to afford a more significant discount applied. On the other hand, hosts who only have 1 - 2 listings may be more likely to be listing the property for supplementary income, which is non essential and therefore they are less price sensitive. 


## Property availability

Some research has suggested that a growing number of AirBnB hosts are moving their properties to month-to-month platforsm that are less lucrative but potentially more reliable. Does the data suggest that this is the case in London, and does this appear to have been exacerbated by lockdown?

### Are more hosts marking their properties as unavailable? Does this appear to have been exacerbated by lockdown in the UK?

Create a dictionary with exact date as keys and monthly date as values.

In [43]:
periods_dict = {                     
 '2019_08_09':'August 2019',
 '2019_09_14':'September 2019',
 '2019_10_15':'October 2019',
 '2019_11_05':'November 2019',
 '2019_12_09':'December 2019',
 '2020_01_09':'January 2020',
 '2020_02_16':'February 2020',
 '2020_03_15':'March 2020',
 '2020_04_14':'April 2020',
 '2020_05_10':'May 2020',
 '2020_06_11':'June 2020',
 '2020_08_24':'August 2020'}

#### Create analytics dataset

First need to get the data. Create a dictionary with the period as keys, and dataframes as the values. Loop through the dataframes that are retrieved and aggregate to get number of listings and maximum availability. From this a value counts is run to get a dataframe which shows whether the properties were unavailable for the full year. 

In [44]:
listing_vol_avail = pd.DataFrame()
for k,v in periods_dict.items():
    print(f'Processing {k}')
    v = v.replace(" ","_")
    df = get_data('calendar_det',k)
    print('   got the calendar data:')
    display(df.head(5))
    df_grp = df.groupby(['listing_id']).agg(**{'num_listings':('listing_id','count'),
                                          'available':('available','max')}).reset_index().reset_index()
    print('   grouped by listing ID to get counts and availability flag')
    display(df_grp.head(5))
    del df
    df_vc = pretty_value_counts(df_grp,'available')
    print('    got distribution count on availability flag')
    del df_grp
    df_vc['period'] = v.replace("_"," ")
    display(df_vc.head(5))
    listing_vol_avail = listing_vol_avail.append(df_vc)
    print('     appending to dataframe')
print('Processed all data')

Processing 2019_08_09
   got the calendar data:


listing_id       date  available  price adjusted_price  minimum_nights  \
0       13913 2019-08-10          1   50.0         $50.00             1.0   
1      158939 2019-08-10          0  110.0        $110.00             2.0   
2      158939 2019-08-11          0  110.0        $110.00             2.0   
3      158939 2019-08-12          0  110.0        $110.00             2.0   
4      158939 2019-08-13          0  110.0        $110.00             2.0   

   maximum_nights  date_month  date_year  
0            29.0           8       2019  
1            14.0           8       2019  
2            14.0           8       2019  
3            14.0           8       2019  
4            14.0           8       2019

   grouped by listing ID to get counts and availability flag


index  listing_id  num_listings  available
0      0       13913           365          1
1      1       15400           365          1
2      2       17402           365          1
3      3       24328           365          1
4      4       25023           365          1

    got distribution count on availability flag


...

   grouped by listing ID to get counts and availability flag


index  listing_id  num_listings  available
0      0       11551           365          1
1      1       13913           365          1
2      2       15400           365          1
3      3       17402           366          1
4      4       17506           365          1

    got distribution count on availability flag


available  count proportion prop_cumul_sum       period
0          1  47140     63.54%         63.54%  August 2020
1          0  27046     36.46%        100.00%  August 2020

     appending to dataframe
Processed all data


The final dataframe

In [45]:
listing_vol_avail

available  count proportion prop_cumul_sum          period
0          1  59816     69.62%         69.62%     August 2019
1          0  26102     30.38%        100.00%     August 2019
0          1  56836     66.65%         66.65%  September 2019
1          0  28437     33.35%        100.00%  September 2019
0          1  55545     66.21%         66.21%    October 2019
1          0  28342     33.79%        100.00%    October 2019
0          1  56973     66.97%         66.97%   November 2019
1          0  28095     33.03%        100.00%   November 2019
0          1  58720     67.91%         67.91%   December 2019
1          0  27749     32.09%        100.00%   December 2019
0          1  57909     66.38%         66.38%    January 2020
1          0  29326     33.62%        100.00%    January 2020
0          1  58261     66.53%         66.53%   February 2020
1          0  29310     33.47%        100.00%   February 2020
0          1  58602     66.50%         66.50%      March 2020
1          0  29527     33.50%        100.00%      March 2020
0          1  54140     62.69%         62.69%      April 2020
1          0  32218     37.31%        100.00%      April 2020
0          1  52723     61.88%         61.88%        May 2020
1          0  32484     38.12%        100.00%        May 2020
0          1  50303     60.09%         60.09%       June 2020
1          0  33408     39.91%        100.00%       June 2020
0          1  47140     63.54%         63.54%     August 2020
1          0  27046     36.46%        100.00%     August 2020

#### Create visualisations

First rename columns and get totals where required.

In [46]:
listing_vol_avail['Listing availability'] = np.where(listing_vol_avail['available']==1,"Available","Unavailable")
listing_vol_avail.rename(columns={'count':'Number of listings','period':'Period','proportion':'Proportion'},inplace=True)
total = listing_vol_avail.groupby(['Period']).agg(**{'Total number of listings':('Number of listings','sum')}).reset_index()                               
listing_vol_avail_tot = listing_vol_avail.merge(total,how='left',on='Period')

Then plot on chart.

In [56]:
fig = px.bar(listing_vol_avail_tot,x='Period',y='Number of listings',color='Listing availability',
      hover_data=['Proportion','Total number of listings'],
      color_discrete_sequence=px.colors.qualitative.Dark24)
fig.update_layout(title=('Listing volume and availability Aug 2019 - 2020'))
fig.update_xaxes(tickangle=90)
fig.show()

#### Conclusion

From the chart it can be seen that there is an increased proportion of unavailable properties around the months of April and May 2020. Unavailabiity did not rise above 33% before these months, and rose to 37% - 40% for April, May and June. This supports our hypothesis that a greater number of hosts would be making their properties unavailable following the global pandemic - either as they move their properties to sites with more stable revenue sources or if they have decided to no longer rent out their room. 

It would be also be interesting to look at this analysis cut by number of rooms the host has - to see whether there is a particular host type that is contributing towards this trend.

## Stay type offering

One final question is whether there has been a change to the minimum stay of properties. It was hypothesised that the minimum stay would have increased to cover for the increased inconvenience of change over days - e.g. cleaning the property, preparing suitable advice for new guests, and facilitating handover days.

### Has there been a change in the minimum nights required for a booking?

Create required functions

In [48]:
def bin_min_nights(min_nights):
    ''' Function which takes in number of nights and bins into categories'''
    if min_nights == 1: return '1'
    elif min_nights in [2,3]: return '2-3'
    elif min_nights in [4,5,6]: return '4-6'
    else: return '7+'

#### Create analytics dataset

In [49]:
agg_df = pd.DataFrame()
for k,v, in periods_dict.items():
    print(f'Processing {v}')
    df = get_data('calendar_det',k)
    print('     got the calendar data:')
    display(df.head(5))
    df_grp = df.groupby(['listing_id']).agg(**{'number_nights_available':('available','sum'),
                                             'median_minimum_nights':('minimum_nights','median'),
                                             'median_maximum_nights':('maximum_nights','median')}).reset_index()
    print('     grouped by listing id to get avg. number of min night booking')
    del df
    df_grp = df_grp[df_grp['number_nights_available'] != 0]
    df_grp['min_nights_bin'] = df_grp['median_minimum_nights'].apply(bin_min_nights)
    display(df_grp.head(5))
    print('     got the distribution count on minimum number of nights')
    df_vc = pretty_value_counts(df_grp,'min_nights_bin')
    del df_grp
    df_vc['Period'] = v
    display(df_vc.head(5))
    agg_df = agg_df.append(df_vc)
    print('     appended to dataframe')
            
print('Processed all data')

Processing August 2019
     got the calendar data:


listing_id       date  available  price adjusted_price  minimum_nights  \
0       13913 2019-08-10          1   50.0         $50.00             1.0   
1      158939 2019-08-10          0  110.0        $110.00             2.0   
2      158939 2019-08-11          0  110.0        $110.00             2.0   
3      158939 2019-08-12          0  110.0        $110.00             2.0   
4      158939 2019-08-13          0  110.0        $110.00             2.0   

   maximum_nights  date_month  date_year  
0            29.0           8       2019  
1            14.0           8       2019  
2            14.0           8       2019  
3            14.0           8       2019  
4            14.0           8       2019

     grouped by listing id to get avg. number of min night booking


listing_id  number_nights_available  median_minimum_nights  \
0       13913                      353                    1.0   
1       15400                      112                   30.0   
2       17402                      284                    3.0   
3       24328                      358                   30.0   
4       25023                        1                    4.0   

   median_maximum_nights min_nights_bin  
0                   29.0              1  
1                   50.0             7+  
2                  365.0            2-3  
3                 1125.0             7+  
4                  100.0            4-6

     got the distribution count on minimum number of nights


...

     grouped by listing id to get avg. number of min night booking


listing_id  number_nights_available  median_minimum_nights  \
0       11551                      236                    2.0   
1       13913                      364                    1.0   
2       15400                      359                   10.0   
3       17402                      357                    4.0   
4       17506                      364                    3.0   

   median_maximum_nights min_nights_bin  
0                 1125.0            2-3  
1                   29.0              1  
2                   50.0             7+  
3                  365.0            4-6  
4                   21.0            2-3

     got the distribution count on minimum number of nights


min_nights_bin  count proportion prop_cumul_sum       Period
0            2-3  19798     42.00%         42.00%  August 2020
1              1  14810     31.42%         73.42%  August 2020
2             7+   6628     14.06%         87.48%  August 2020
3            4-6   5904     12.52%        100.00%  August 2020

     appended to dataframe
Processed all data


In [50]:
agg_df

min_nights_bin  count proportion prop_cumul_sum          Period
0             2-3  26512     44.32%         44.32%     August 2019
1               1  19148     32.01%         76.33%     August 2019
2             4-6   7976     13.33%         89.67%     August 2019
3              7+   6180     10.33%        100.00%     August 2019
0             2-3  25079     44.13%         44.13%  September 2019
..            ...    ...        ...            ...             ...
3             4-6   6285     12.49%        100.00%       June 2020
0             2-3  19798     42.00%         42.00%     August 2020
1               1  14810     31.42%         73.42%     August 2020
2              7+   6628     14.06%         87.48%     August 2020
3             4-6   5904     12.52%        100.00%     August 2020

[48 rows x 5 columns]

#### Create visualisations

In [51]:

fig = go.Figure()
data = agg_df
fig.add_trace(go.Scatter(x=data[data['min_nights_bin']=='1']['Period'],
                             y=data[data['min_nights_bin']=='1']['count'],name='1 night'))
fig.add_trace(go.Scatter(x=data[data['min_nights_bin']=='2-3']['Period'],
                         y=data[data['min_nights_bin']=='2-3']['count'],name='2-3 nights'))
fig.add_trace(go.Scatter(x=data[data['min_nights_bin']=='4-6']['Period'],
                         y=data[data['min_nights_bin']=='4-6']['count'],name='4-6 nights'))
fig.add_trace(go.Scatter(x=data[data['min_nights_bin']=='7+']['Period'],
                         y=data[data['min_nights_bin']=='7+']['count'],name='7+ nights'))
fig.update_layout(title=('Minimum night stay in AirBnB properties'))
fig.update_xaxes(tickangle=90,title='Period')
fig.update_yaxes(title='Number of properties')

fig.show()

#### Conclusion

From the chart it can be seen that the most popular minimum stay is consistently for 2-3 nights, followed by 1 night. The volume of properties with these minimum stay types have been decreased since March 2020 (in line with the trend of reduced volume of properties since then found in section 4.2.) There consistently a similar volume of properties with a minimum stay of 4-6 nights or over 7 nights. Between August 2019 and Apri there were more properties with a stay of 4-6 nights than 6 nights. In April this trend was reversed, and from then onwards there were more properties with a minimum stay of 7 nights. This observation supports the hypothesis that there would be an increase in the minimum stay at properties around the time of lockdown.